# Similarity score comparison

In [1]:
!pip install matchms
!pip install pubchempy
!pip install rdkit-pypi
!pip install spec2vec --user

In [1]:
import os
import numpy as np
from matchms.importing import load_from_mgf
import matplotlib.pyplot as plt
import pubchempy
import pandas as pd
from itertools import compress
from rdkit import Chem
from rdkit.Chem import Draw

In [2]:
from matchms import calculate_scores
from matchms.similarity import CosineGreedy
from matchms.similarity import ModifiedCosine
from matchms.similarity import NeutralLossesCosine

In [3]:
import gensim
from spec2vec import Spec2Vec
from matchms.filtering import default_filters
from matchms.filtering import normalize_intensities

In [4]:
path_data = "C:/Users/naake/Documents/GitHub/SimilarityHackathon/data/"
file_mgf_reference = os.path.join(path_data, "GNPS-LIBRARY.mgf")
reference_spectra = list(load_from_mgf(file_mgf_reference))

# Expand grid function

Define a function that calculates all possible combinations of parameters. Iterate over the data frame in the following.

In [5]:
from itertools import product
import pandas as pd

def expand_grid(dictionary):
   return pd.DataFrame([row for row in product(*dictionary.values())], 
                       columns=dictionary.keys())


combinations_cosine = {
    'tolerance': [0.005, 0.01], 
    'mz_power': [0, 0.5, 1, 2], 
    'intensity_power': [0, 0.5, 1, 2]}
combinations_modified_cosine = {
    'tolerance': [0.005, 0.01], 
    'mz_power': [0, 0.5, 1, 2], 
    'intensity_power': [0, 0.5, 1, 2]}
combinations_neutralloss_cosine = {
    'tolerance': [0.01], 
    'mz_power': [0, 1, 2], 
    'intensity_power': [0, 0.5, 1],
    'ignore_peaks_above_precursor': [True]}
combinations_spec2vec = {
    'intensity_weighting_power': [0, 0.5, 1, 2],
    'allowed_missing_percentage': [5, 10, 20]}

## expand the grids for the parameter spaces
combinations_cosine = expand_grid(combinations_cosine)
combinations_modified_cosine = expand_grid(combinations_modified_cosine)
combinations_neutralloss_cosine = expand_grid(combinations_neutralloss_cosine)
combinations_spec2vec = expand_grid(combinations_spec2vec)

## Spec2Vec

In [6]:
path_model = "C:/Users/naake/Documents/GitHub/SimilarityHackathon/data/"
filename_model = "spec2vec_AllPositive_ratio05_filtered_201101_iter_15.model"
filename = os.path.join(path_model, filename_model)
model = gensim.models.Word2Vec.load(filename)

In [7]:
def peak_processing(spectrum):
    spectrum = default_filters(spectrum)
    spectrum = normalize_intensities(spectrum)
    return spectrum

reference_s2v_spectra = [peak_processing(s) for s in reference_spectra  if len(s.peaks) != 0]

2023-01-18 22:03:02,324:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 981.54 with new one: 981.54
2023-01-18 22:03:02,326:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 940.25 with new one: 940.25
2023-01-18 22:03:02,348:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 456.1 with new one: 456.1
2023-01-18 22:03:02,357:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 545.0 with new one: 545.0
2023-01-18 22:03:02,371:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 314.116 with new one: 314.116
2023-01-18 22:03:02,383:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 667.115 with new one: 667.115
2023-01-18 22:03:02,395:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 689.0 with new one: 689.0
2023-01-18 22:03:02,405:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1025.61 with new one: 1025.61
2023-01-18 22:03:02,415:WARNING:matchms:

2023-01-18 22:03:03,178:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 345.24 with new one: 345.24
2023-01-18 22:03:03,187:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 727.32 with new one: 727.32
2023-01-18 22:03:03,200:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 749.288 with new one: 749.288
2023-01-18 22:03:03,214:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 404.131 with new one: 404.131
2023-01-18 22:03:03,223:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 426.202 with new one: 426.202
2023-01-18 22:03:03,244:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 601.358 with new one: 601.358
2023-01-18 22:03:03,254:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 623.339 with new one: 623.339
2023-01-18 22:03:03,264:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 410.282 with new one: 410.282
2023-01-18 22:03:03,275:WARN

2023-01-18 22:03:04,028:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 628.0 with new one: 628.0
2023-01-18 22:03:04,036:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 501.0 with new one: 501.0
2023-01-18 22:03:04,055:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1532.0 with new one: 1532.0
2023-01-18 22:03:04,072:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1533.0 with new one: 1533.0
2023-01-18 22:03:04,087:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1502.5 with new one: 1502.5
2023-01-18 22:03:04,093:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1503.6 with new one: 1503.6
2023-01-18 22:03:04,110:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1533.4 with new one: 1533.4
2023-01-18 22:03:04,124:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1502.47 with new one: 1502.47
2023-01-18 22:03:04,137:WARNING:matchms:in

2023-01-18 22:03:04,917:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 372.05 with new one: 372.05
2023-01-18 22:03:04,923:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 360.0 with new one: 360.0
2023-01-18 22:03:04,937:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 579.0 with new one: 579.0
2023-01-18 22:03:04,949:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 601.6 with new one: 601.6
2023-01-18 22:03:04,958:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 905.0 with new one: 905.0
2023-01-18 22:03:04,973:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 907.0 with new one: 907.0
2023-01-18 22:03:04,984:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 928.0 with new one: 928.0
2023-01-18 22:03:04,996:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 789.4 with new one: 789.4
2023-01-18 22:03:05,009:WARNING:matchms:interpret_pepm

2023-01-18 22:03:05,785:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 244.0 with new one: 244.0
2023-01-18 22:03:05,797:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 211.0 with new one: 211.0
2023-01-18 22:03:05,802:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 272.0 with new one: 272.0
2023-01-18 22:03:05,814:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 195.0 with new one: 195.0
2023-01-18 22:03:05,828:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 225.0 with new one: 225.0
2023-01-18 22:03:05,836:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 224.0 with new one: 224.0
2023-01-18 22:03:05,849:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 277.0 with new one: 277.0
2023-01-18 22:03:05,865:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 181.0 with new one: 181.0
2023-01-18 22:03:05,876:WARNING:matchms:interpret_pepmas

...

2023-01-18 22:05:46,117:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 861.394 with new one: 861.394
2023-01-18 22:05:46,133:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 875.411 with new one: 875.411
2023-01-18 22:05:46,149:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 876.414 with new one: 876.414
2023-01-18 22:05:46,166:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 945.454 with new one: 945.454
2023-01-18 22:05:46,181:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 958.485 with new one: 958.485
2023-01-18 22:05:46,197:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 981.502 with new one: 981.502
2023-01-18 22:05:46,212:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1128.57 with new one: 1128.57
2023-01-18 22:05:46,229:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 662.37 with new one: 662.37
2023-01-18 22:05:46,244:WA

2023-01-18 22:05:47,090:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 554.798 with new one: 554.798
2023-01-18 22:05:47,107:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 559.293 with new one: 559.293
2023-01-18 22:05:47,123:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 566.316 with new one: 566.316
2023-01-18 22:05:47,139:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 568.317 with new one: 568.317
2023-01-18 22:05:47,155:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 577.834 with new one: 577.834
2023-01-18 22:05:47,170:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 577.835 with new one: 577.835
2023-01-18 22:05:47,186:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 582.329 with new one: 582.329
2023-01-18 22:05:47,186:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 582.33 with new one: 582.33
2023-01-18 22:05:47,202:WA

2023-01-18 22:05:48,005:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1216.68 with new one: 1216.68
2023-01-18 22:05:48,013:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1278.69 with new one: 1278.69
2023-01-18 22:05:48,025:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1279.7 with new one: 1279.7
2023-01-18 22:05:48,025:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1300.68 with new one: 1300.68
2023-01-18 22:05:48,041:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1363.75 with new one: 1363.75
2023-01-18 22:05:48,049:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 343.045 with new one: 343.045
2023-01-18 22:05:48,063:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 640.238 with new one: 640.238
2023-01-18 22:05:48,081:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1038.38 with new one: 1038.38
2023-01-18 22:05:48,112:WA

2023-01-18 22:05:49,093:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 670.858 with new one: 670.858
2023-01-18 22:05:49,109:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 682.376 with new one: 682.376
2023-01-18 22:05:49,126:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 682.878 with new one: 682.878
2023-01-18 22:05:49,142:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 689.364 with new one: 689.364
2023-01-18 22:05:49,174:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 690.418 with new one: 690.418
2023-01-18 22:05:49,190:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 710.904 with new one: 710.904
2023-01-18 22:05:49,208:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 712.401 with new one: 712.401
2023-01-18 22:05:49,224:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 713.385 with new one: 713.385
2023-01-18 22:05:49,241:

2023-01-18 22:05:50,146:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1154.66 with new one: 1154.66
2023-01-18 22:05:50,162:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1238.66 with new one: 1238.66
2023-01-18 22:05:50,178:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1278.69 with new one: 1278.69
2023-01-18 22:05:50,194:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1131.62 with new one: 1131.62
2023-01-18 22:05:50,194:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1109.59 with new one: 1109.59
2023-01-18 22:05:50,210:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1091.59 with new one: 1091.59
2023-01-18 22:05:50,227:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1301.73 with new one: 1301.73
2023-01-18 22:05:50,243:WARNING:matchms:interpret_pepmass:Overwriting existing precursor_mz 1108.59 with new one: 1108.59
2023-01-18 22:05:50,259:

In [8]:
combinations_spec2vec

intensity_weighting_power  allowed_missing_percentage
0                         0.0                           5
1                         0.0                          10
2                         0.0                          20
3                         0.5                           5
4                         0.5                          10
5                         0.5                          20
6                         1.0                           5
7                         1.0                          10
8                         1.0                          20
9                         2.0                           5
10                        2.0                          10
11                        2.0                          20

In [13]:
new_colnames = []
new_cols = []

for index, row in combinations_spec2vec.iterrows():
    print(index)
    spec2vec_similarity = Spec2Vec(model=model,
                               intensity_weighting_power=row["intensity_weighting_power"],
                               allowed_missing_percentage=row["allowed_missing_percentage"])
    spec2vec_scores = calculate_scores(reference_s2v_spectra, reference_s2v_spectra, spec2vec_similarity,
                          is_symmetric=False)
    scores = spec2vec_scores.scores
    SCORES = np.zeros(shape=scores.shape)
    for i in range(scores.shape[0]):
        for j in range(scores.shape[1]):
            SCORES[i][j] = scores[i][j]#[0]
    SCORES_df = pd.DataFrame(SCORES)
    
    ## add row- and colnames to data.frame
    SCORES_df.index = [s.metadata["spectrum_id"] for s in reference_s2v_spectra]
    SCORES_df.columns = SCORES_df.index
    SCORES_df['rows'] = SCORES_df.index

    ## from wide to long
    SCORES_df = pd.melt(SCORES_df, id_vars ='rows', value_vars = list(SCORES_df.columns[:-1]))
    new_column = 'Spec2Vec' + "_" + str(row['intensity_weighting_power']) + "_" + str(row['allowed_missing_percentage'])
    new_colnames.append(new_column)
    new_cols.append(SCORES_df['value'].values)
    
    SCORES_df = SCORES_df.rename(columns={'value': 'Spec2Vec' + "_" + str(row['intensity_weighting_power']) + "_" + str(row['allowed_missing_percentage'])})
    

0
2023-01-18 22:23:38,062:WARNING:spec2vec:vector_operations:('Missing percentage (30.77%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,071:WARNING:spec2vec:vector_operations:('Missing percentage (6.25%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,085:WARNING:spec2vec:vector_operations:('Missing percentage (10.29%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,098:WARNING:spec2vec:vector_operations:('Missing percentage (15.40%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,101:WARNING:spec2vec:vector_operations:('Missing percentage (7.

2023-01-18 22:23:38,625:WARNING:spec2vec:vector_operations:('Missing percentage (19.83%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,627:WARNING:spec2vec:vector_operations:('Missing percentage (21.76%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,634:WARNING:spec2vec:vector_operations:('Missing percentage (18.07%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,723:WARNING:spec2vec:vector_operations:('Missing percentage (32.35%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,723:WARNING:spec2vec:vector_operations:('Missing percentage (33.

2023-01-18 22:23:38,960:WARNING:spec2vec:vector_operations:('Missing percentage (16.47%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,965:WARNING:spec2vec:vector_operations:('Missing percentage (13.64%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,972:WARNING:spec2vec:vector_operations:('Missing percentage (23.00%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,975:WARNING:spec2vec:vector_operations:('Missing percentage (33.49%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:38,977:WARNING:spec2vec:vector_operations:('Missing percentage (28.

2023-01-18 22:23:39,243:WARNING:spec2vec:vector_operations:('Missing percentage (6.00%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,246:WARNING:spec2vec:vector_operations:('Missing percentage (5.31%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,257:WARNING:spec2vec:vector_operations:('Missing percentage (7.66%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,269:WARNING:spec2vec:vector_operations:('Missing percentage (8.89%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,276:WARNING:spec2vec:vector_operations:('Missing percentage (11.75%)

2023-01-18 22:23:39,721:WARNING:spec2vec:vector_operations:('Missing percentage (75.80%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,731:WARNING:spec2vec:vector_operations:('Missing percentage (71.20%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,744:WARNING:spec2vec:vector_operations:('Missing percentage (71.20%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,754:WARNING:spec2vec:vector_operations:('Missing percentage (75.20%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-18 22:23:39,764:WARNING:spec2vec:vector_operations:('Missing percentage (72.

...

2023-01-19 00:09:31,545:WARNING:spec2vec:vector_operations:('Missing percentage (37.35%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:33,533:WARNING:spec2vec:vector_operations:('Missing percentage (99.49%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:33,677:WARNING:spec2vec:vector_operations:('Missing percentage (70.38%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:33,709:WARNING:spec2vec:vector_operations:('Missing percentage (99.99%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:33,724:WARNING:spec2vec:vector_operations:('Missing percentage (99.

2023-01-19 00:09:46,091:WARNING:spec2vec:vector_operations:('Missing percentage (86.71%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:46,370:WARNING:spec2vec:vector_operations:('Missing percentage (46.31%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:46,386:WARNING:spec2vec:vector_operations:('Missing percentage (84.26%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:46,454:WARNING:spec2vec:vector_operations:('Missing percentage (97.29%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:46,486:WARNING:spec2vec:vector_operations:('Missing percentage (47.

2023-01-19 00:09:49,098:WARNING:spec2vec:vector_operations:('Missing percentage (35.47%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:49,104:WARNING:spec2vec:vector_operations:('Missing percentage (73.08%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:49,119:WARNING:spec2vec:vector_operations:('Missing percentage (74.57%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:49,119:WARNING:spec2vec:vector_operations:('Missing percentage (68.12%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:09:49,135:WARNING:spec2vec:vector_operations:('Missing percentage (99.

2023-01-19 00:10:19,134:WARNING:spec2vec:vector_operations:('Missing percentage (26.62%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:10:19,902:WARNING:spec2vec:vector_operations:('Missing percentage (62.53%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:10:20,479:WARNING:spec2vec:vector_operations:('Missing percentage (27.44%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:10:21,858:WARNING:spec2vec:vector_operations:('Missing percentage (25.55%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:10:25,990:WARNING:spec2vec:vector_operations:('Missing percentage (99.

2023-01-19 00:10:57,243:WARNING:spec2vec:vector_operations:('Missing percentage (50.56%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')
2023-01-19 00:10:57,259:WARNING:spec2vec:vector_operations:('Missing percentage (98.92%) is above set maximum. An empty vector will be returned.', 'Consider retraining the used model or change the `allowed_missing_percentage`.')


In [14]:
for i, colname in enumerate(new_colnames):
    SCORES_df[colname] = list(new_cols[i])

In [15]:
SCORES_df

rows            variable  Spec2Vec_2.0_20.0  \
0          CCMSLIB00000001547  CCMSLIB00000001547           1.000000   
1          CCMSLIB00000001548  CCMSLIB00000001547           0.225854   
2          CCMSLIB00000001549  CCMSLIB00000001547           0.009459   
3          CCMSLIB00000001550  CCMSLIB00000001547           0.200955   
4          CCMSLIB00000001551  CCMSLIB00000001547           0.041285   
...                       ...                 ...                ...   
162970751  CCMSLIB00010129217  CCMSLIB00010129221          -0.051378   
162970752  CCMSLIB00010129218  CCMSLIB00010129221           0.859743   
162970753  CCMSLIB00010129219  CCMSLIB00010129221           0.999873   
162970754  CCMSLIB00010129220  CCMSLIB00010129221           0.999784   
162970755  CCMSLIB00010129221  CCMSLIB00010129221           1.000000   

           Spec2Vec_0.0_5.0  Spec2Vec_0.0_10.0  Spec2Vec_0.0_20.0  \
0                  1.000000           1.000000           1.000000   
1                  0.488936           0.488936           0.488936   
2                 -0.166572          -0.166572          -0.166572   
3                  0.205473           0.205473           0.205473   
4                 -0.161674          -0.161674          -0.161674   
...                     ...                ...                ...   
162970751          0.006951           0.006951           0.006951   
162970752          0.719353           0.719353           0.719353   
162970753          0.577909           0.577909           0.577909   
162970754          0.443625           0.443625           0.443625   
162970755          1.000000           1.000000           1.000000   

           Spec2Vec_0.5_5.0  Spec2Vec_0.5_10.0  Spec2Vec_0.5_20.0  \
0                  1.000000           1.000000           1.000000   
1                  0.502385           0.502385           0.502385   
2                 -0.066494          -0.066494          -0.066494   
3                  0.197767           0.197767           0.197767   
4                 -0.070635          -0.070635          -0.070635   
...                     ...                ...                ...   
162970751         -0.030488          -0.030488          -0.030488   
162970752          0.864900           0.864900           0.864900   
162970753          0.935467           0.935467           0.935467   
162970754          0.881790           0.881790           0.881790   
162970755          1.000000           1.000000           1.000000   

           Spec2Vec_1.0_5.0  Spec2Vec_1.0_10.0  Spec2Vec_1.0_20.0  \
0                  1.000000           1.000000           1.000000   
1                  0.472098           0.472098           0.472098   
2                  0.050126           0.050126           0.050126   
3                  0.203799           0.203799           0.203799   
4                  0.034687           0.034687           0.034687   
...                     ...                ...                ...   
162970751         -0.058455          -0.058455          -0.058455   
162970752          0.875463           0.875463           0.875463   
162970753          0.992311           0.992311           0.992311   
162970754          0.987035           0.987035           0.987035   
162970755          1.000000           1.000000           1.000000   

           Spec2Vec_2.0_5.0  Spec2Vec_2.0_10.0  
0                  1.000000           1.000000  
1                  0.225854           0.225854  
2                  0.009459           0.009459  
3                  0.200955           0.200955  
4                  0.041285           0.041285  
...                     ...                ...  
162970751         -0.051378          -0.051378  
162970752          0.859743           0.859743  
162970753          0.999873           0.999873  
162970754          0.999784           0.999784  
162970755          1.000000           1.000000  

[162970756 rows x 14 columns]

In [16]:
## only keep the comparisions between same collision energies
SCORES_df["matching_CE"] = SCORES_df.apply(lambda x: x["rows"].split("_")[-1] == x["variable"].split("_")[-1], axis=1)

MemoryError: 

In [ ]:
SCORES_df = SCORES_df[SCORES_df["matching_CE"]]

In [17]:
SCORES_df.to_csv("similarities_Spec2Vec2_GNPS.csv")

## Neutral loss score

In [18]:
combinations_neutralloss_cosine

tolerance  mz_power  intensity_power  ignore_peaks_above_precursor
0       0.01         0              0.0                          True
1       0.01         0              0.5                          True
2       0.01         0              1.0                          True
3       0.01         1              0.0                          True
4       0.01         1              0.5                          True
5       0.01         1              1.0                          True
6       0.01         2              0.0                          True
7       0.01         2              0.5                          True
8       0.01         2              1.0                          True

In [26]:
reference_spectra_red = [s for s in reference_spectra if len(s.peaks) > 2]
reference_spectra_red = [s for s in reference_spectra_red if s.metadata["precursor_mz"] > 0]

In [ ]:
new_colnames = []
new_cols = []

for index, row in combinations_neutralloss_cosine.iterrows():
    print(index)
    neutralloss_similarity = NeutralLossesCosine(tolerance=row["tolerance"],
            mz_power=row["mz_power"], intensity_power=row["intensity_power"],
            ignore_peaks_above_precursor=row["ignore_peaks_above_precursor"])
    neutralloss_scores = calculate_scores(reference_spectra_red, reference_spectra_red, neutralloss_similarity,
                          is_symmetric=True)
    scores = neutralloss_scores.scores
    SCORES = np.zeros(shape=scores.shape)
    for i in range(scores.shape[0]):
        for j in range(scores.shape[1]):
            SCORES[i][j] = scores[i][j][0]
    SCORES_df = pd.DataFrame(SCORES)
    
    ## add row- and colnames to data.frame
    SCORES_df.index = [s.metadata["spectrum_id"] for s in reference_spectra_red]
    SCORES_df.columns = SCORES_df.index
    SCORES_df['rows'] = SCORES_df.index

    ## from wide to long
    SCORES_df = pd.melt(SCORES_df, id_vars ='rows', value_vars = list(SCORES_df.columns[:-1]))
    new_column = 'Neutralloss' + "_" + str(row['tolerance']) + "_" + str(row['mz_power']) + "_" + str(row["intensity_power"]) + "_" + str(row["ignore_peaks_above_precursor"])
    new_colnames.append(new_column)
    new_cols.append(SCORES_df['value'].values)
    
    SCORES_df = SCORES_df.rename(columns={'value': new_column})
    

0


In [ ]:
for i, colname in enumerate(new_colnames):
    SCORES_df[colname] = list(new_cols[i])

In [ ]:
SCORES_df

In [ ]:
## only keep the comparisions between same collision energies
SCORES_df["matching_CE"] = SCORES_df.apply(lambda x: x["rows"].split("_")[-1] == x["variable"].split("_")[-1], axis=1)

In [ ]:
SCORES_df = SCORES_df[SCORES_df["matching_CE"]]

In [ ]:
SCORES_df.to_csv("similarities_NeutralLoss_GNPS.csv")